# Aula Teórica 5: Persistência da Informação

## Armazenamento em memória secundária: ficheiros

### Abertura: open(nome, modo)

Modos de abertura de um ficheiro:
* "r" - Read - Valor por omissão. Abre o ficheiro para leitura, devolve error se o ficheiro não existir;
* "a" - Append - Abre o ficheiro para acrescentar, cria o ficheiro se este não existir;
* "w" - Write - Abre o ficheiro para escrever, cria o ficheiro se este não existir, apaga o conteúdo se este existir;
* "x" - Create - Cria o ficheiro, devolve error se o ficheiro já existir.

Parâmetro adicional ao modo:
* "t" - Text - Valor por omissão. Ficheiro textual;
* "b" - Binary - Ficheiro binário, por exemplo, imagens.

In [1]:
f = open("bdArtigos.json", "rt")
f2 = open("bdArtigos.json", "r")
f3 = open("bdArtigos.json")

### Leitura do conteúdo

In [ ]:
f4 = open("demo.txt")
print(f4.read())

Uma linha de cada vez, iterando pelas linhas...

In [ ]:
f4 = open("demo.txt")
print(f4.readline())
print(f4.readline())

In [ ]:
f4 = open("demo.txt")
i=1
for linha in f4:
    print(str(i) + " :: " + linha)
    i = i+1

### Fechar um ficheiro: devemos fazê-lo no fim...

In [ ]:
f4 = open("demo.txt")
i=1
for linha in f4:
    print(str(i) + " :: " + linha)
    i = i+1
f4.close()

### Escrever num ficheiro

In [ ]:
f5 = open("demo.txt", "a")
f5.write("Agora o ficheiro tem mais conteúdo!")
f5.close()

f5 = open("demo.txt", "r")
print(f5.read())

## O nosso problema: a BD bibliográfica - Como guardar em ficheiro?

In [7]:
arts = [{'chaveCit': 'RHA2008', 'titulo': 'Álgebra Documental', 
        'autores': [('jcr', 'José Carlos Ramalho'), ('prh', 'Pedro Rangel Henriques'), ('jj', 'José João Almeida')], 
        'ano': 2008, 'local': 'Twente - Holanda'}, 
    {'chaveCit': 'RHA1998', 'titulo': 'Utilização do email pedagogicamente', 
        'autores': [('jcr', 'José Carlos Ramalho'), ('prh', 'Pedro Rangel Henriques'), ('jj', 
        'José João Almeida')], 'ano': 1999, 'local': 'Universidade do Minho'}]

### Hipótese 1: no "meu" ficheiro de texto
__Que forma irão ter os registos?__

`chaveCit::titulo::autor1#autor2#...#autorn::ano::local`

Aplicado ao nosso exemplo:

`RHA2008::Álgebra Documental::jcr,José Carlos Ramalho#prh,Pedro Rangel Henriques#jj,José João Almeida::2008::Twente - Holanda

RHA1998::Utilização do email pedagogicamente::jcr,José Carlos Ramalho#prh,Pedro Rangel Henriques#jj,José João Almeida::1999::Universidade do Minho`

In [ ]:
# Guardar a BD no ficheiro
def guardarBD(bd, fnome):
    f = open(fnome, 'w', encoding='utf-8')
    sep = "::"
    myReg = ""
    for art in arts:
        myReg = art['chaveCit'] + sep + art['titulo'] + sep
        i = 1
        for (id, nome) in art['autores']:
            myReg = myReg + id + "," + nome
            if i < len(art['autores']):
                myReg = myReg + "#"
            else:
                myReg = myReg + "::"
            i = i+1
        myReg = myReg + str(art['ano']) + sep + art['local']
        myReg = myReg + "\n"
        f.write(myReg)

guardarBD(arts, "bdArtigos.txt")
print("Foram guardados " + str(len(arts)) + " registos.")

In [ ]:
# Carregar a BD dum ficheiro
def extraiAutores(linha):
    res = []
    autores = linha.split("#")
    for a in autores:
        acampos = a.split(",")
        res.append((acampos[0],acampos[1]))
    return res
    
def carregarBD(fnome):
    bd = []
    f = open(fnome)
    for linha in f:
        myReg = {}
        campos = linha.split("::")
        myReg['chaveCit'] = campos[0]
        myReg['titulo'] = campos[1]
        myReg['autores'] = extraiAutores(campos[2])
        myReg['ano'] = campos[3]
        myReg['local'] = campos[4]
        bd.append(myReg)
    return bd

teste = carregarBD("bdArtigos.txt")
print(teste)

In [ ]:
# Mais umas reutilizações do código já escrito
# Inserir mais alguns registos e guardar
# ...

### Hipótese 2: em JSON

(fazer uma visita guiada a [json.org](https://www.json.org/json-en.html))

In [21]:
# Guardar a BD em JSON
import json

def guardarBD(bd, fnome):
    with open(fnome, 'w', encoding='utf-8') as f:
        json.dump(bd, f, ensure_ascii=False, indent=4)

guardarBD(arts, "bdArtigos.json")

In [ ]:
# Carregar a BD dum ficheiro em JSON
def carregarBD(fnome):
    f = open(fnome)
    bd = json.load(f)
    return bd

teste = []
teste = carregarBD("bdArtigos.json")
print(teste)

O campo autores não veio no formato pretendido. Altera a função de carregamento de modo a colocar tudo no formato esperado.